In [37]:
import pandas as pd
import unicodedata
import re
from fuzzywuzzy import process

In [38]:
# Définir les noms de colonnes selon la documentation GeoNames
fieldnames = [
    "geonameid", "name", "asciiname", "alternatenames", "latitude",
    "longitude", "feature_class", "feature_code", "country_code", "cc2",
    "admin1_code", "admin2_code", "admin3_code", "admin4_code",
    "population", "elevation", "dem", "timezone", "modification_date"
]

# Lire le fichier cities15000.txt dans un DataFrame
df = pd.read_csv("cities15000.txt", 
                 delimiter="\t", 
                 names=fieldnames, 
                 encoding="utf-8", 
                 header=None)

# Conversion des colonnes numériques
df["latitude"] = df["latitude"].astype(float)
df["longitude"] = df["longitude"].astype(float)
df["population"] = pd.to_numeric(df["population"], errors="coerce").fillna(0).astype(int)

# Transformer la colonne alternatenames en liste (en séparant par la virgule)
df["alternatenames"] = df["alternatenames"].fillna("").apply(lambda x: x.split(",") if x else [])


In [39]:
df[df['name'] == 'Parys']

geonameid   name asciiname         alternatenames  latitude  longitude  \
29517     966166  Parys     Parys  [Paris, Parys, Парис]  -26.9033   27.45727   

      feature_class feature_code country_code  cc2 admin1_code admin2_code  \
29517             P        PPLA3           ZA  NaN          03        DC20   

      admin3_code admin4_code  population  elevation   dem  \
29517       FS203         NaN       71319        NaN  1398   

                  timezone modification_date  
29517  Africa/Johannesburg        2024-01-18

In [40]:
# --- Fonctions utilitaires ---
def normalize_text(text):
    """
    Normalise une chaîne de caractères en :
    - Remplaçant les tirets par des espaces
    - Supprimant les accents
    - Convertissant en minuscules
    - Retirant la ponctuation inutile
    """
    text = text.replace("-", " ")
    text = unicodedata.normalize('NFKD', text).encode('ASCII', 'ignore').decode('utf-8')
    text = text.lower()
    text = re.sub(r'[^\w\s]', '', text)
    return re.sub(r'\s+', ' ', text).strip()

In [41]:
# Création d'une colonne qui contient la liste de tous les noms normalisés pour chaque ville.
df['all_names_list'] = df.apply(
    lambda row: [normalize_text(row['name'])] + [normalize_text(n) for n in row['alternatenames']],
    axis=1
)

In [42]:
# --- Fonction de classification ---

def classify_city_df(input_name, df, country_code=None, threshold=95):
    """
    Recherche dans le DataFrame la ville correspondant à input_name en tenant compte du code pays si précisé.
    La recherche se fait d'abord par correspondance exacte dans la liste des noms normalisés,
    puis par fuzzy matching sur la concaténation de ces noms.
    
    :param input_name: le nom de la ville à rechercher
    :param df: le DataFrame contenant les informations des villes
    :param country_code: (optionnel) le code ISO du pays à filtrer (ex. "FR", "AD", etc.)
    :param threshold: seuil de similarité pour le fuzzy matching
    :return: une ligne du DataFrame contenant 'name', 'geonameid', 'latitude', 'longitude' et 'country_code' si une correspondance est trouvée, sinon None.
    """
    norm_input = normalize_text(input_name)
    
    # Filtrer le DataFrame sur le code pays si précisé
    if country_code:
        df_country = df[df['country_code'] == country_code]
    else:
        df_country = df.copy()
    
    # Recherche exacte : on regarde si la liste de noms normalisés contient norm_input
    exact_matches = df_country[df_country['all_names_list'].apply(lambda names: norm_input in names)]
    if not exact_matches.empty:
        return exact_matches.iloc[0]
    else:
        # Pour le fuzzy matching, on crée une chaîne unique par ligne (concaténation de tous les noms normalisés)
        df_country = df_country.copy()  # Pour éviter les avertissements sur la modification d'une vue
        df_country['all_names_str'] = df_country['all_names_list'].apply(lambda names: ' '.join(names))
        choices = df_country['all_names_str'].tolist()
        best_match, score = process.extractOne(norm_input, choices, scorer=fuzz.token_set_ratio)
        if score >= threshold:
            matched_row = df_country[df_country['all_names_str'] == best_match].iloc[0]
            return matched_row
        else:
            return None

In [43]:
# --- Test de robustesse avec une série d'inputs similaires ---

# Exemple d'inputs avec des variations (certains présents dans cities15000, d'autres variantes)
# Exemple de test avec différents inputs et codes pays
test_inputs = [
    ("Les Escaldes", "AD"),       # Andorre : devrait correspondre à "les Escaldes"
    ("Andorra-la-Vella", "AD"),   # Variante avec tirets pour "Andorra la Vella"
    ("Paris", "FR"),              # Paris en France
    ("Paris", "US"),              # Paris mais avec un code pays qui ne correspond pas (ne devrait rien trouver)
]

for input_name, c_code in test_inputs:
    result = classify_city_df(input_name, df, country_code=c_code)
    if result is not None:
        official = result['name']
        geonameid = result['geonameid']
        lat = result['latitude']
        lon = result['longitude']
        country = result['country_code']
        print(f"Input: {input_name} (Country: {c_code}) -> Official: {official}, GeoNameID: {geonameid}, Country: {country}, Coordinates: ({lat}, {lon})")
    else:
        print(f"Input: {input_name} (Country: {c_code}) -> Aucune correspondance trouvée")

Input: Les Escaldes (Country: AD) -> Official: les Escaldes, GeoNameID: 3040051, Country: AD, Coordinates: (42.50729, 1.53414)
Input: Andorra-la-Vella (Country: AD) -> Official: Andorra la Vella, GeoNameID: 3041563, Country: AD, Coordinates: (42.50779, 1.52109)
Input: Paris (Country: FR) -> Official: Paris, GeoNameID: 2988507, Country: FR, Coordinates: (48.85341, 2.3488)
Input: Paris (Country: US) -> Official: Paris, GeoNameID: 4717560, Country: US, Coordinates: (33.66094, -95.55551)


In [44]:
for i in mapping:
    if mapping[i] == "Paris":
        print(mapping)

In [45]:
print(mapping)

{'escaldes engordany': ('les Escaldes', 3040051, 42.50729, 1.53414), 'les escaldes': ('les Escaldes', 3040051, 42.50729, 1.53414), 'ehskaldes ehndzhordani': ('les Escaldes', 3040051, 42.50729, 1.53414), '': ('Chitungwiza', 1106542, -18.01274, 31.07555), 'esukarudesuengorudani jiao qu': ('les Escaldes', 3040051, 42.50729, 1.53414), 'escaldes': ('les Escaldes', 3040051, 42.50729, 1.53414), 'lai sai si ka er de en ge er da': ('les Escaldes', 3040051, 42.50729, 1.53414), 'andorra a velha': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'andoro malnova': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'andorra tuan': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'andorra la velja': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'alv': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'andorra': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'andorra la vielha': ('Andorra la Vella', 3041563, 42.50779, 1.52109), 'andora la vela': ('Andorra la Vella', 3041563, 42.50779, 1.52109)